### Imports

In [1]:
# Pandas
import pandas as pd
# Plotly
import plotly
from plotly.offline import init_notebook_mode, iplot
import plotly.graph_objs as go
import plotly.figure_factory as ff
init_notebook_mode(connected=True)
#Mapbox
from mapboxgl.utils import *
from mapboxgl.viz import *

### Analysis based on data from Ministry of Home Affairs

In [2]:
df_home_affairs = pd.read_csv("data_sources/home_affairs.csv")

In [3]:
df_home_affairs.head()

District  Number of Death  Number of Missing  Number of Injured  \
0  Taplejung              NaN                NaN                NaN   
1      Jhapa              3.0                1.0                2.0   
2       Ilam              1.0                3.0                NaN   
3  Panchthar              1.0                NaN                NaN   
4     Morang              5.0                3.0                1.0   

  Temporarily displaced Household  
0                               1  
1                             NaN  
2                             NaN  
3                             NaN  
4                           1,539

### Plot Function

In [4]:
def plot_bar(x, y):
    return (go.Figure(data=[go.Bar(
                x=x, y=y,
                text=y,
                textposition='auto',
            )]))

### 10 Most Affected Districts

#### Number of deaths

In [5]:
df_deaths = df_home_affairs.sort_values(['Number of Death'], ascending=False).head(10)[['District', 'Number of Death']]

In [6]:
df_deaths

District  Number of Death
17     Rautahat             10.0
24     Lalitpur              6.0
13       Siraha              6.0
26    Makwanpur              5.0
4        Morang              5.0
7       Bhojpur              5.0
21     Sindhuli              5.0
10  Okhaldhunga              4.0
14     Dhanusha              4.0
15    Mahottari              4.0

In [7]:
iplot(plot_bar(x=df_deaths['District'], y=df_deaths['Number of Death']))

#### Number of injured

In [8]:
df_injured = df_home_affairs.sort_values(['Number of Injured'], ascending=False).head(10)[['District', 'Number of Injured']]

In [9]:
df_injured

District  Number of Injured
26  Makwanpur                5.0
25  Kathmandu                5.0
17   Rautahat                5.0
21   Sindhuli                3.0
9    Dhankuta                3.0
11    Udaypur                3.0
1       Jhapa                2.0
7     Bhojpur                2.0
13     Siraha                2.0
15  Mahottari                2.0

In [10]:
iplot(plot_bar(x=df_injured['District'], y=df_injured['Number of Injured']))

#### Number of missing

In [11]:
df_missing = df_home_affairs.sort_values(['Number of Missing'], ascending=False).head(10)[['District', 'Number of Missing']]

In [12]:
df_missing

District  Number of Missing
32      Dolpa                8.0
2        Ilam                3.0
4      Morang                3.0
21   Sindhuli                3.0
11    Udaypur                2.0
15  Mahottari                2.0
1       Jhapa                1.0
5     Sunsari                1.0
14   Dhanusha                1.0
17   Rautahat                1.0

In [13]:
iplot(plot_bar(x=df_missing['District'], y=df_missing['Number of Missing']))

#### Temporarily displaced Household

In [14]:
df_home_affairs['Temporarily displaced Household'] = df_home_affairs['Temporarily displaced Household'].str.replace(',', '')
df_home_affairs['Temporarily displaced Household'] = df_home_affairs['Temporarily displaced Household'].fillna(0).astype(int)

In [15]:
df_household = df_home_affairs.sort_values(['Temporarily displaced Household'], ascending=False).head(6)[['District', 'Temporarily displaced Household']]

In [16]:
df_household

District  Temporarily displaced Household
13    Siraha                             5000
16   Sarlahi                             2400
18      Bara                             1665
4     Morang                             1539
17  Rautahat                             1110
19     Parsa                              120

In [17]:
iplot(plot_bar(x=df_household['District'], y=df_household['Temporarily displaced Household']))

### Mapping

In [18]:
df_geojson = pd.read_json('data_sources/map.geojson')

In [19]:
df_geojson.head()

features               type
0  {'properties': {'name': 'Humla', 'death': 1}, ...  FeatureCollection
1  {'properties': {'name': 'Darchula', 'death': 2...  FeatureCollection
2  {'properties': {'name': 'Bajhang', 'death': 3}...  FeatureCollection
3  {'properties': {'name': 'Mugu'}, 'geometry': {...  FeatureCollection
4  {'properties': {'name': 'Bajura'}, 'geometry':...  FeatureCollection

In [20]:
df_home_affairs.set_index("District", inplace=True)

In [21]:
def add_data(features):
    name = features.get('properties').get('name')
    if (name in df_home_affairs.index):
        death = df_home_affairs.loc[name]['Number of Death']
        injured = df_home_affairs.loc[name]['Number of Injured']
        missing = df_home_affairs.loc[name]['Number of Missing']
        displaced = df_home_affairs.loc[name]['Temporarily displaced Household']
        features['properties'] = {'name': name, 'death': death, 'injured': injured, 'missing':missing, 'displaced':displaced}
        return features

In [22]:
df_geojson.features.apply(add_data)

0                                                  None
1                                                  None
2                                                  None
3                                                  None
4                                                  None
5                                                  None
6     {'properties': {'name': 'Dolpa', 'death': 3.0,...
7                                                  None
8                                                  None
9                                                  None
10                                                 None
11                                                 None
12                                                 None
13                                                 None
14                                                 None
15    {'properties': {'name': 'Kanchanpur', 'death':...
16                                                 None
17                                              

In [23]:
features = df_geojson['features'].values.tolist()

In [24]:
my_dict = {"type":"FeatureCollection", "features":features}

In [25]:
token  = "pk.eyJ1IjoiYXl1c2hzdWJlZGkiLCJhIjoiY2pweGp4MzV3MTl3ZzN5bzB0bzl4Y2dwMSJ9.MPh0n0FdMwYunrIHjz8lxQ"

### Deaths

In [26]:
viz = ChoroplethViz(my_dict, 
                     access_token=token,
                     color_property='death',
                     color_stops=create_color_stops([0, 2, 5, 8, 10], colors='YlOrRd'),
                     color_function_type='interpolate',
                     line_stroke='--',
                     line_color='rgb(128,0,38)',
                     line_width=1,
                     opacity=0.8,
                     center=(84, 28.5), 
                     zoom=6
                    )
viz.show()

### Missing

In [27]:
viz = ChoroplethViz(my_dict, 
                     access_token=token,
                     color_property='missing',
                     color_stops=create_color_stops([0, 2, 5, 8, 10], colors='YlOrRd'),
                     color_function_type='interpolate',
                     line_stroke='--',
                     line_color='rgb(128,0,38)',
                     line_width=1,
                     opacity=0.8,
                     center=(84, 28.5), 
                     zoom=6
                    )
viz.show()

### Injured

In [28]:
viz = ChoroplethViz(my_dict, 
                     access_token=token,
                     color_property='injured',
                     color_stops=create_color_stops([0, 2, 5, 8, 10], colors='YlOrRd'),
                     color_function_type='interpolate',
                     line_stroke='--',
                     line_color='rgb(128,0,38)',
                     line_width=1,
                     opacity=0.8,
                     center=(84, 28.5), 
                     zoom=6
                    )
viz.show()

### Temporarily Displaced Household

In [32]:
viz = ChoroplethViz(my_dict, 
                     access_token=token,
                     color_property='displaced',
                     color_stops=create_color_stops([0, 200, 500, 800, 1000], colors='YlOrRd'),
                     color_function_type='interpolate',
                     line_stroke='--',
                     line_color='rgb(128,0,38)',
                     line_width=1,
                     opacity=0.8,
                     center=(84, 28.5), 
                     zoom=6
                    )
viz.show()